# Simulating Constitutive Processes of semantic change within heterogeneous populations of speakers

In [5]:
# basic imports
import os
import torch
import numpy as np
import pandas as pd
from tqdm.notebook import tqdm

# project code imports
from mod.one_hot_agent import *
from mod.plot import *
from mod.network import *

##### Hyper parameters

In [6]:
model_version = 'sn-shuffle'

In [7]:
no_agents = 20
no_connections = 5
add_vocab_in = 50
semantic_features = 3
starting_observations = 5
starting_uncertainty = .2
words_per_semantic_feature = 5
new_environment_prob = .25
shuffle_vocab_in = 100
enforce_word_feature_mapping = False

In [8]:
model_path = os.path.join('html',model_version)
if not os.path.exists(model_path):
    os.mkdir(model_path)

## Simple nteraction across repeated turns in a randomly generated environment

In [9]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [10]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [11]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [12]:
# and set the number of iterations
turns = 300

In [13]:
vocab_dif = []

In [14]:
for rd in tqdm(range(turns)):
    env = starting_env.sample()

    #shuffle vocab
    if (rd % shuffle_vocab_in) == 0:
        for agent in net.agents:
            new_index = np.random.choice(len(agent.vocab), size=(len(agent.vocab),), replace=False)
            agent.vocab = agent.vocab[new_index]

    net.interaction(env, 3)
    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [15]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [16]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [17]:
fig.write_html(
    os.path.join(model_path,'Randomly-Generated-Environment.html')
)

## Random environment and introduction of new terms

In [18]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [19]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [20]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [21]:
# and set the number of iterations
turns = 300

In [22]:
vocab_dif = []

In [23]:
for rd in tqdm(range(turns)):
    env = starting_env.sample()

    new_vocab_round = ((rd % add_vocab_in) == 0) & (rd != 0)

    #shuffle vocab
    if (rd % shuffle_vocab_in) == 0:
        for agent in net.agents:
            new_index = np.random.choice(len(agent.vocab), size=(len(agent.vocab),), replace=False)
            agent.vocab = agent.vocab[new_index]

    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [24]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [25]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.write_html(
    os.path.join(model_path,'Randomly-Generated-Environment-and-Introducing-Novel-Terms.html')
)
fig.show()

## Changing environment

In [26]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [27]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [28]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [29]:
# and set the number of iterations
turns = 300

In [30]:
vocab_dif = []

In [31]:
for rd in tqdm(range(turns)):

    new_env_prob = torch.rand(size=(1,))
    if new_env_prob > new_environment_prob:
        starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

    env = starting_env.sample()

    new_vocab_round = False

    #shuffle vocab
    if (rd % shuffle_vocab_in) == 0:
        for agent in net.agents:
            new_index = np.random.choice(len(agent.vocab), size=(len(agent.vocab),), replace=False)
            agent.vocab = agent.vocab[new_index]

    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [32]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [33]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [34]:
fig.write_html(
    os.path.join(model_path,'Suddenly-Changing-Environment.html')
)

## Changing environment and introduction of new terms

In [35]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [36]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [37]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [38]:
# and set the number of iterations
turns = 300

In [39]:
vocab_dif = []

In [40]:
for rd in tqdm(range(turns)):

    new_env_prob = torch.rand(size=(1,))
    if new_env_prob > new_environment_prob:
        starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

    env = starting_env.sample()

    new_vocab_round = ((rd % add_vocab_in) == 0) & (rd != 0)

    #shuffle vocab
    if (rd % shuffle_vocab_in) == 0:
        for agent in net.agents:
            new_index = np.random.choice(len(agent.vocab), size=(len(agent.vocab),), replace=False)
            agent.vocab = agent.vocab[new_index]

    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [41]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [42]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [43]:
fig.write_html(
    os.path.join(model_path,'Suddenly-Changing-Environment-and-Introducing-Novel-Terms.html')
)

## Stochastic environment

In [44]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [45]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [46]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [47]:
# and set the number of iterations
turns = 300

In [48]:
vocab_dif = []

In [49]:
for rd in tqdm(range(turns)):

    env = starting_env.sample()
    starting_env.loc = env

    new_vocab_round = False

    #shuffle vocab
    if (rd % shuffle_vocab_in) == 0:
        for agent in net.agents:
            new_index = np.random.choice(len(agent.vocab), size=(len(agent.vocab),), replace=False)
            agent.vocab = agent.vocab[new_index]

    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [50]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [51]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [52]:
fig.write_html(
    os.path.join(model_path,'Stochastically-Changing-Environment.html')
)

## Stochastic environment and introduction of new terms

In [53]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [54]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [55]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [56]:
# and set the number of iterations
turns = 30000

In [57]:
vocab_dif = []

In [58]:
for rd in tqdm(range(turns)):

    env = starting_env.sample()
    starting_env.loc = env

    new_vocab_round = ((rd % add_vocab_in) == 0) & (rd != 0)

    #shuffle vocab
    if (rd % shuffle_vocab_in) == 0:
        for agent in net.agents:
            new_index = np.random.choice(len(agent.vocab), size=(len(agent.vocab),), replace=False)
            agent.vocab = agent.vocab[new_index]

    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/30000 [00:00<?, ?it/s]

In [59]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [60]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [61]:
fig.write_html(
    os.path.join(model_path,'Stochastically-Changing-Environment-and-Introducing-Novel-Terms.html')
)

## Sudden and stochastic environment

In [62]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [63]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [64]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [65]:
# and set the number of iterations
turns = 300

In [66]:
vocab_dif = []

In [67]:
for rd in tqdm(range(turns)):

    new_env_prob = torch.rand(size=(1,))
    if new_env_prob > new_environment_prob:
        starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

    env = starting_env.sample()
    starting_env.loc = env

    new_vocab_round = False

    #shuffle vocab
    if (rd % shuffle_vocab_in) == 0:
        for agent in net.agents:
            new_index = np.random.choice(len(agent.vocab), size=(len(agent.vocab),), replace=False)
            agent.vocab = agent.vocab[new_index]

    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [68]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [69]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [70]:
fig.write_html(
    os.path.join(model_path,'Suddenly-and-Stochastically-Changing-Environment.html')
)

## Sudden and stochastic environment, plus introduction of new terms

In [71]:
starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

In [72]:
net = social_network(
    k_agents=no_agents,
    vocab_size=words_per_semantic_feature,
    connections_per_agent=no_connections,
    semantic_dimensions=semantic_features,
    starting_observations=starting_observations,
    starting_uncertainty=starting_uncertainty,
    enforcing=enforce_word_feature_mapping
)

In [73]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [74]:
# and set the number of iterations
turns = 300

In [75]:
vocab_dif = []

In [76]:
for rd in tqdm(range(turns)):

    new_env_prob = torch.rand(size=(1,))
    if new_env_prob > new_environment_prob:
        starting_env = torch.distributions.MultivariateNormal(torch.randn(size=(1,semantic_features)), covariance_matrix=torch.eye(semantic_features) * .2)

    env = starting_env.sample()
    starting_env.loc = env

    new_vocab_round = ((rd % add_vocab_in) == 0) & (rd != 0)

    #shuffle vocab
    if (rd % shuffle_vocab_in) == 0:
        for agent in net.agents:
            new_index = np.random.choice(len(agent.vocab), size=(len(agent.vocab),), replace=False)
            agent.vocab = agent.vocab[new_index]

    net.interaction(env, 3, new_vocab_round)

    vocab_dif += [{'agent':i + 1, 'interaction': rd, 'Δ P(w|m)':val} for i,val in enumerate(net.similarity_heatmap().mean(dim=-1).tolist())]

vocab_dif = pd.DataFrame(vocab_dif)

  0%|          | 0/300 [00:00<?, ?it/s]

In [77]:
fig = heatmap(
    net.similarity_heatmap(),
    x_labels=['agent_'+str(i+1) for i in range(len(net.agents))],
    y_labels=['agent_'+str(i+1) for i in range(len(net.agents))]
)
fig.show()

In [78]:
fig = multi_agent_update_plot_from_df(vocab_dif)
fig.update_layout(
    # title='Dyadic interaction in a random environment',
    yaxis_title='Δ P(w|m)',
    xaxis_title='interactions'
)
fig.show()

In [79]:
fig.write_html(
    os.path.join(model_path,'Suddenly-and-Stochastically-Changing-Environment-and-Introducing-Novel-Terms.html')
)